In [1]:
import os
import numpy as np
import caffe
import cv2
import datetime
import matplotlib.pyplot as plt
# display plots in this notebook
%matplotlib inline

gpu_mode = True
gpu_id = 0
data_root =  '/root/local/data/ILSVRC2012/' 
val_file = '/root/local/data/ILSVRC_2012_val.txt'
save_log = '/root/local/log{}.txt'.format(datetime.datetime.now().strftime('%Y%m%d%H%M%S'))
model_weights = '/root/local/inception-v3.caffemodel'
model_deploy = '/root/local/deploy_inception-v3_crop_395.prototxt'
prob_layer = 'prob'
class_num = 1000
base_size = 395 # short size
crop_size = 395
mean_value = np.array([128.0, 128.0, 128.0])  # BGR
#mean_value = np.array([102.9801, 115.9465, 122.7717])  # BGR
std = np.array([128.0, 128.0, 128.0])  # BGR
#std = np.array([1.0, 1.0, 1.0])  # BGR
crop_num = 1  # 1 and others for center(single)-crop, 12 for mirror(12)-crop, 144 for multi(144)-crop
batch_size = 1
top_k = (1, 5)

if gpu_mode:
    caffe.set_mode_gpu()
    caffe.set_device(gpu_id)
else:
    caffe.set_mode_cpu()
net = caffe.Net(model_deploy, model_weights, caffe.TEST)

In [2]:
def eval_batch():
    eval_images =  []
    ground_truth = []
    f = open(val_file, 'r')
    for i in f:
        eval_images.append(os.path.basename(i.strip().split(' ')[0]))
        ground_truth.append(int(i.strip().split(' ')[1]))
    f.close()

    skip_num = 0
    eval_len = len(eval_images)
    accuracy = np.zeros(len(top_k))
    #eval_len = 1000
    start_time = datetime.datetime.now()
    for i in xrange(eval_len - skip_num):
        _img = cv2.imread(data_root + eval_images[i + skip_num])
        _img = cv2.resize(_img, (int(_img.shape[1] * base_size / min(_img.shape[:2])),
                                 int(_img.shape[0] * base_size / min(_img.shape[:2])))
                          )
        _img = image_preprocess(_img)

        score_vec = np.zeros(class_num, dtype=np.float32)
        crops = []
        if crop_num == 1:
            crops.append(center_crop(_img))
        elif crop_num == 12:
            crops.extend(mirror_crop(_img))
        elif crop_num == 144:
            crops.extend(multi_crop(_img))
        else:
            crops.append(center_crop(_img))

        iter_num = int(len(crops) / batch_size)
        for j in xrange(iter_num):
            score_vec += caffe_process(np.asarray(crops, dtype=np.float32)[j*batch_size:(j+1)*batch_size])
        score_index = (-score_vec / len(crops)).argsort()

        print 'Testing image: ' + str(i + 1) + '/' + str(eval_len - skip_num) + '  ' + str(score_index[0]) + '/' + str(
            ground_truth[i + skip_num]),
        for j in xrange(len(top_k)):
            if ground_truth[i + skip_num] in score_index[:top_k[j]]:
                accuracy[j] += 1
            tmp_acc = float(accuracy[j]) / float(i + 1)
            if top_k[j] == 1:
                print '\ttop_' + str(top_k[j]) + ':' + str(tmp_acc),
            else:
                print 'top_' + str(top_k[j]) + ':' + str(tmp_acc)

    end_time = datetime.datetime.now()
    
    w = open(save_log, 'w')
    s1 = 'Evaluation process ends at: {}. \nTime cost is: {}. '.format(str(end_time), str(end_time - start_time))
    s2 = '\nThe model is: {}. \nThe val file is: {}. \n{} images has been tested, crop_num is: {}, base_size is: {}, ' \
         'crop_size is: {}.'.format(model_weights, val_file, str(eval_len), str(crop_num), str(base_size), str(crop_size))
    s3 = '\nThe mean value is: ({}, {}, {}).'.format(str(mean_value[0]), str(mean_value[1]), str(mean_value[2]))
    s4 = ''
    for i in xrange(len(top_k)):
        _acc = float(accuracy[i]) / float(eval_len)
        s4 += '\nAccuracy of top_{} is: {}; correct num is {}.'.format(str(top_k[i]), str(_acc), str(int(accuracy[i])))
    print s1, s2, s3, s4
    w.write(s1 + s2 + s3 + s4)
    w.close()

def image_preprocess(img):
    #plt.imshow(img)
    #plt.show()
    b, g, r = cv2.split(img)
    return cv2.merge([(b-mean_value[0])/std[0], (g-mean_value[1])/std[1], (r-mean_value[2])/std[2]])


def center_crop(img): # single crop
    short_edge = min(img.shape[:2])
    if short_edge < crop_size:
        return
    yy = int((img.shape[0] - crop_size) / 2)
    xx = int((img.shape[1] - crop_size) / 2)
    return img[yy: yy + crop_size, xx: xx + crop_size]


def over_sample(img):  # 12 crops of image
    short_edge = min(img.shape[:2])
    if short_edge < crop_size:
        return
    yy = int((img.shape[0] - crop_size) / 2)
    xx = int((img.shape[1] - crop_size) / 2)
    sample_list = [img[:crop_size, :crop_size], img[-crop_size:, -crop_size:], img[:crop_size, -crop_size:],
                   img[-crop_size:, :crop_size], img[yy: yy + crop_size, xx: xx + crop_size],
                   cv2.resize(img, (crop_size, crop_size))]
    return sample_list


def mirror_crop(img):  # 12*len(size_list) crops
    crop_list = []
    img_resize = cv2.resize(img, (base_size, base_size))
    mirror = img_resize[:, ::-1]
    crop_list.extend(over_sample(img_resize))
    crop_list.extend(over_sample(mirror))
    return crop_list


def multi_crop(img):  # 144(12*12) crops
    crop_list = []
    #size_list = [256, 288, 320, 352]  # crop_size: 224
    # size_list = [270, 300, 330, 360]  # crop_size: 235
    size_list = [320, 352, 384, 416]  # crop_size: 299
    # size_list = [352, 384, 416, 448]  # crop_size: 320
    short_edge = min(img.shape[:2])
    for i in size_list:
        img_resize = cv2.resize(img, (img.shape[1] * i / short_edge, img.shape[0] * i / short_edge))
        yy = int((img_resize.shape[0] - i) / 2)
        xx = int((img_resize.shape[1] - i) / 2)
        for j in xrange(3):
            left_center_right = img_resize[yy * j: yy * j + i, xx * j: xx * j + i]
            mirror = left_center_right[:, ::-1]
            crop_list.extend(over_sample(left_center_right))
            crop_list.extend(over_sample(mirror))
    return crop_list


def caffe_process(_input):
    _input = _input.transpose(0, 3, 1, 2)
    #plt.imshow(_input[1:])
    #plt.show()
    #print(_input.shape)
    net.blobs['data'].reshape(*_input.shape)
    net.blobs['data'].data[...] = _input
    net.forward()

    return np.sum(net.blobs[prob_layer].data, axis=0)

In [3]:
eval_batch()

Testing image: 1/50000  486/489 	top_1:0.0 top_5:1.0
Testing image: 2/50000  360/360 	top_1:0.5 top_5:1.0
Testing image: 3/50000  123/170 	top_1:0.333333333333 top_5:1.0
Testing image: 4/50000  821/821 	top_1:0.5 top_5:1.0
Testing image: 5/50000  296/296 	top_1:0.6 top_5:1.0
Testing image: 6/50000  481/481 	top_1:0.666666666667 top_5:1.0
Testing image: 7/50000  12/12 	top_1:0.714285714286 top_5:1.0
Testing image: 8/50000  703/703 	top_1:0.75 top_5:1.0
Testing image: 9/50000  598/598 	top_1:0.777777777778 top_5:1.0
Testing image: 10/50000  163/163 	top_1:0.8 top_5:1.0
Testing image: 11/50000  648/648 	top_1:0.818181818182 top_5:1.0
Testing image: 12/50000  10/10 	top_1:0.833333333333 top_5:1.0
Testing image: 13/50000  72/72 	top_1:0.846153846154 top_5:1.0
Testing image: 14/50000  285/285 	top_1:0.857142857143 top_5:1.0
Testing image: 15/50000  553/553 	top_1:0.866666666667 top_5:1.0
Testing image: 16/50000  5/5 	top_1:0.875 top_5:1.0
Testing image: 17/50000  224/647 	top_1:0.82352941176

Testing image: 119/50000  695/868 	top_1:0.781512605042 top_5:0.966386554622
Testing image: 120/50000  597/597 	top_1:0.783333333333 top_5:0.966666666667
Testing image: 121/50000  689/595 	top_1:0.776859504132 top_5:0.96694214876
Testing image: 122/50000  700/700 	top_1:0.77868852459 top_5:0.967213114754
Testing image: 123/50000  969/969 	top_1:0.780487804878 top_5:0.967479674797
Testing image: 124/50000  454/451 	top_1:0.774193548387 top_5:0.967741935484
Testing image: 125/50000  631/630 	top_1:0.768 top_5:0.968
Testing image: 126/50000  816/816 	top_1:0.769841269841 top_5:0.968253968254
Testing image: 127/50000  56/56 	top_1:0.771653543307 top_5:0.968503937008
Testing image: 128/50000  396/397 	top_1:0.765625 top_5:0.96875
Testing image: 129/50000  884/884 	top_1:0.767441860465 top_5:0.968992248062
Testing image: 130/50000  9/9 	top_1:0.769230769231 top_5:0.969230769231
Testing image: 131/50000  287/287 	top_1:0.770992366412 top_5:0.969465648855
Testing image: 132/50000  304/304 	top

Testing image: 228/50000  203/203 	top_1:0.767543859649 top_5:0.969298245614
Testing image: 229/50000  459/459 	top_1:0.768558951965 top_5:0.96943231441
Testing image: 230/50000  768/768 	top_1:0.769565217391 top_5:0.969565217391
Testing image: 231/50000  619/619 	top_1:0.770562770563 top_5:0.969696969697
Testing image: 232/50000  287/799 	top_1:0.76724137931 top_5:0.965517241379
Testing image: 233/50000  152/152 	top_1:0.768240343348 top_5:0.965665236052
Testing image: 234/50000  682/682 	top_1:0.769230769231 top_5:0.965811965812
Testing image: 235/50000  364/364 	top_1:0.770212765957 top_5:0.965957446809
Testing image: 236/50000  654/449 	top_1:0.766949152542 top_5:0.966101694915
Testing image: 237/50000  206/206 	top_1:0.767932489451 top_5:0.966244725738
Testing image: 238/50000  615/615 	top_1:0.768907563025 top_5:0.966386554622
Testing image: 239/50000  764/984 	top_1:0.765690376569 top_5:0.962343096234
Testing image: 240/50000  915/993 	top_1:0.7625 top_5:0.9625
Testing image: 24

Testing image: 338/50000  789/789 	top_1:0.754437869822 top_5:0.958579881657
Testing image: 339/50000  938/528 	top_1:0.752212389381 top_5:0.955752212389
Testing image: 340/50000  36/36 	top_1:0.752941176471 top_5:0.955882352941
Testing image: 341/50000  847/847 	top_1:0.75366568915 top_5:0.956011730205
Testing image: 342/50000  625/625 	top_1:0.754385964912 top_5:0.956140350877
Testing image: 343/50000  185/185 	top_1:0.755102040816 top_5:0.956268221574
Testing image: 344/50000  760/760 	top_1:0.755813953488 top_5:0.956395348837
Testing image: 345/50000  543/592 	top_1:0.753623188406 top_5:0.95652173913
Testing image: 346/50000  300/300 	top_1:0.754335260116 top_5:0.956647398844
Testing image: 347/50000  238/238 	top_1:0.755043227666 top_5:0.956772334294
Testing image: 348/50000  205/205 	top_1:0.755747126437 top_5:0.956896551724
Testing image: 349/50000  774/774 	top_1:0.756446991404 top_5:0.957020057307
Testing image: 350/50000  112/112 	top_1:0.757142857143 top_5:0.957142857143
Tes

Testing image: 448/50000  343/343 	top_1:0.772321428571 top_5:0.962053571429
Testing image: 449/50000  311/311 	top_1:0.772828507795 top_5:0.962138084633
Testing image: 450/50000  171/171 	top_1:0.773333333333 top_5:0.962222222222
Testing image: 451/50000  658/658 	top_1:0.773835920177 top_5:0.962305986696
Testing image: 452/50000  284/284 	top_1:0.774336283186 top_5:0.962389380531
Testing image: 453/50000  996/996 	top_1:0.774834437086 top_5:0.962472406181
Testing image: 454/50000  571/571 	top_1:0.775330396476 top_5:0.962555066079
Testing image: 455/50000  708/708 	top_1:0.775824175824 top_5:0.962637362637
Testing image: 456/50000  161/161 	top_1:0.776315789474 top_5:0.962719298246
Testing image: 457/50000  86/86 	top_1:0.776805251641 top_5:0.962800875274
Testing image: 458/50000  565/565 	top_1:0.777292576419 top_5:0.96288209607
Testing image: 459/50000  846/846 	top_1:0.777777777778 top_5:0.962962962963
Testing image: 460/50000  713/713 	top_1:0.778260869565 top_5:0.963043478261
Te

...

Testing image: 49470/50000  536/536 	top_1:0.799231857692 top_5:0.95182939155
Testing image: 49471/50000  84/84 	top_1:0.799235915991 top_5:0.951830365264
Testing image: 49472/50000  992/992 	top_1:0.799239974127 top_5:0.951831338939
Testing image: 49473/50000  558/558 	top_1:0.799244032098 top_5:0.951832312575
Testing image: 49474/50000  670/670 	top_1:0.799248089906 top_5:0.951833286171
Testing image: 49475/50000  358/242 	top_1:0.799231935321 top_5:0.951834259727
Testing image: 49476/50000  920/920 	top_1:0.799235993209 top_5:0.951835233244
Testing image: 49477/50000  189/189 	top_1:0.799240050933 top_5:0.951836206722
Testing image: 49478/50000  603/605 	top_1:0.79922389749 top_5:0.951837180161
Testing image: 49479/50000  507/507 	top_1:0.799227955294 top_5:0.95183815356
Testing image: 49480/50000  431/431 	top_1:0.799232012935 top_5:0.95183912692
Testing image: 49481/50000  996/996 	top_1:0.799236070411 top_5:0.95184010024
Testing image: 49482/50000  707/707 	top_1:0.799240127723 t

Testing image: 49575/50000  245/245 	top_1:0.799112455875 top_5:0.951770045386
Testing image: 49576/50000  224/224 	top_1:0.799116507988 top_5:0.951771018235
Testing image: 49577/50000  364/451 	top_1:0.799100389293 top_5:0.951771991044
Testing image: 49578/50000  620/620 	top_1:0.799104441486 top_5:0.951772963815
Testing image: 49579/50000  540/796 	top_1:0.799088323685 top_5:0.951753766716
Testing image: 49580/50000  252/252 	top_1:0.799092375958 top_5:0.951754739814
Testing image: 49581/50000  80/51 	top_1:0.799076259051 top_5:0.951755712874
Testing image: 49582/50000  532/964 	top_1:0.799060142794 top_5:0.951736517284
Testing image: 49583/50000  290/290 	top_1:0.79906419539 top_5:0.951737490672
Testing image: 49584/50000  404/404 	top_1:0.799068247822 top_5:0.951738464021
Testing image: 49585/50000  449/449 	top_1:0.799072300091 top_5:0.95173943733
Testing image: 49586/50000  1/1 	top_1:0.799076352196 top_5:0.9517404106
Testing image: 49587/50000  586/586 	top_1:0.799080404138 top_

Testing image: 49684/50000  163/163 	top_1:0.79913050479 top_5:0.951775219387
Testing image: 49685/50000  770/770 	top_1:0.79913454765 top_5:0.951776189997
Testing image: 49686/50000  612/618 	top_1:0.799118463954 top_5:0.951777160568
Testing image: 49687/50000  971/768 	top_1:0.799102380904 top_5:0.951778131101
Testing image: 49688/50000  885/885 	top_1:0.799106424086 top_5:0.951779101594
Testing image: 49689/50000  302/761 	top_1:0.799090341927 top_5:0.951780072048
Testing image: 49690/50000  904/776 	top_1:0.799074260415 top_5:0.951781042463
Testing image: 49691/50000  777/777 	top_1:0.799078303918 top_5:0.951782012839
Testing image: 49692/50000  932/932 	top_1:0.799082347259 top_5:0.951782983176
Testing image: 49693/50000  930/930 	top_1:0.799086390437 top_5:0.951783953474
Testing image: 49694/50000  682/682 	top_1:0.799090433453 top_5:0.951784923733
Testing image: 49695/50000  291/291 	top_1:0.799094476305 top_5:0.951785893953
Testing image: 49696/50000  454/454 	top_1:0.799098518

Testing image: 49792/50000  195/195 	top_1:0.799044023136 top_5:0.951759318766
Testing image: 49793/50000  954/954 	top_1:0.799048058964 top_5:0.951760287591
Testing image: 49794/50000  701/989 	top_1:0.799032011889 top_5:0.951761256376
Testing image: 49795/50000  754/754 	top_1:0.799036047796 top_5:0.951762225123
Testing image: 49796/50000  767/767 	top_1:0.799040083541 top_5:0.951763193831
Testing image: 49797/50000  568/568 	top_1:0.799044119124 top_5:0.9517641625
Testing image: 49798/50000  746/746 	top_1:0.799048154544 top_5:0.95176513113
Testing image: 49799/50000  221/337 	top_1:0.799032109078 top_5:0.951766099721
Testing image: 49800/50000  68/68 	top_1:0.799036144578 top_5:0.951767068273
Testing image: 49801/50000  21/21 	top_1:0.799040179916 top_5:0.951768036786
Testing image: 49802/50000  606/606 	top_1:0.799044215092 top_5:0.951769005261
Testing image: 49803/50000  391/391 	top_1:0.799048250105 top_5:0.951769973696
Testing image: 49804/50000  949/949 	top_1:0.799052284957 t

Testing image: 49901/50000  139/139 	top_1:0.798981984329 top_5:0.951784533376
Testing image: 49902/50000  95/95 	top_1:0.798986012585 top_5:0.951785499579
Testing image: 49903/50000  715/715 	top_1:0.798990040679 top_5:0.951786465744
Testing image: 49904/50000  778/778 	top_1:0.798994068612 top_5:0.951787431869
Testing image: 49905/50000  655/655 	top_1:0.798998096383 top_5:0.951788397956
Testing image: 49906/50000  357/357 	top_1:0.799002123993 top_5:0.951789364004
Testing image: 49907/50000  673/673 	top_1:0.799006151442 top_5:0.951790330014
Testing image: 49908/50000  45/45 	top_1:0.799010178729 top_5:0.951791295985
Testing image: 49909/50000  766/766 	top_1:0.799014205855 top_5:0.951792261917
Testing image: 49910/50000  762/762 	top_1:0.799018232819 top_5:0.95179322781
Testing image: 49911/50000  340/340 	top_1:0.799022259622 top_5:0.951794193665
Testing image: 49912/50000  120/120 	top_1:0.799026286264 top_5:0.951795159481
Testing image: 49913/50000  565/565 	top_1:0.799030312744